You can run either this notebook locally (if you have all the dependencies and a GPU) or on Google Colab.

Instructions for setting up Colab are as follows:
1. Open a new Python 3 notebook.
2. Import this notebook from GitHub (File -> Upload Notebook -> "GITHUB" tab -> copy/paste GitHub URL)
3. Connect to an instance with a GPU (Runtime -> Change runtime type -> select "GPU" for hardware accelerator)
4. Run this cell to set up dependencies.

In [1]:
import os
# either provide a path to local NeMo repository with NeMo already installed or git clone
BRANCH = 'chooper-dl-msdiar'

# option #1: local path to NeMo repo with NeMo already installed
NEMO_DIR_PATH = "NeMo"

# option #2: download NeMo repo
if 'google.colab' in str(get_ipython()) or not os.path.exists(NEMO_DIR_PATH):
  ! git clone -b $BRANCH https://github.com/chooper1/NeMo
  %cd NeMo
  ! python -m pip install git+https://github.com/chooper1/NeMo.git@$BRANCH#egg=nemo_toolkit[all]
  %cd ..

Cloning into 'NeMo'...
remote: Enumerating objects: 118682, done.
remote: Counting objects: 100% (128/128), done.
remote: Compressing objects: 100% (35/35), done.
remote: Total 118682 (delta 103), reused 116 (delta 93), pack-reused 118554
Receiving objects: 100% (118682/118682), 261.47 MiB | 17.70 MiB/s, done.
Resolving deltas: 100% (90367/90367), done.
/home/chooper/projects/chooper_dl_msdiar/NeMo/tutorials/tools/NeMo
  Cloning https://github.com/chooper1/NeMo.git (to revision chooper-dl-msdiar) to /tmp/pip-install-3b8nuyw5/nemo-toolkit_022e19b39bb643d7ac930b2b140cc2f8
  Running command git clone -q https://github.com/chooper1/NeMo.git /tmp/pip-install-3b8nuyw5/nemo-toolkit_022e19b39bb643d7ac930b2b140cc2f8
  Running command git checkout -b chooper-dl-msdiar --track origin/chooper-dl-msdiar
  Switched to a new branch 'chooper-dl-msdiar'
  Branch 'chooper-dl-msdiar' set up to track remote branch 'chooper-dl-msdiar' from 'origin'.
  Resolved https://github.com/chooper1/NeMo.git to commit

  Created wheel for nemo-toolkit: filename=nemo_toolkit-1.11.0rc0-py3-none-any.whl size=3486472 sha256=b8d5dd13d7076d39c96c8270887b7388731ebfedcacace02f49040f470a3670d
  Stored in directory: /tmp/pip-ephem-wheel-cache-3_vyz8mh/wheels/58/76/32/34c0c61c4909a7232051afd551e641405137f26226f3201754
Successfully built nemo-toolkit
  Attempting uninstall: nemo-toolkit
    Found existing installation: nemo-toolkit 1.11.0rc0
    Uninstalling nemo-toolkit-1.11.0rc0:
      Successfully uninstalled nemo-toolkit-1.11.0rc0
/home/chooper/projects/chooper_dl_msdiar/NeMo/tutorials/tools


In [2]:
import json
import os
import wget
import numpy as np

! pip install cmake
! pip install https://github.com/DavidDiazGuerra/gpuRIR/zipball/master

  Using cached https://github.com/DavidDiazGuerra/gpuRIR/zipball/master


# Introduction

This tutorial shows how to use the speech data simulator to generate synthetic multispeaker audio sessions that can be used to train or evaluate models for multispeaker ASR or speaker diarization. This tool aims to address the lack of labelled multispeaker training data and to help models deal with overlapping speech.

# Step 1: Download Required Datasets

The LibriSpeech dataset and corresponding word alignments are required for generating synthetic multispeaker audio sessions. For simplicity, only the dev-clean dataset is used for generating synthetic sessions.

In [3]:
!mkdir LibriSpeech
!python NeMo/scripts/dataset_processing/get_librispeech_data.py \
  --data_root LibriSpeech \
  --data_sets dev_clean

100%|████████████████████████████████████████| 322M/322M [00:18<00:00, 18.0MB/s]
100%|███████████████████████████████████████████| 97/97 [00:19<00:00,  4.91it/s]


The LibriSpeech forced word alignments are from the following repository: https://github.com/CorentinJ/librispeech-alignments

The google drive link is: https://drive.google.com/file/d/1WYfgr31T-PPwMcxuAq09XZfHQO5Mw8fE/view?usp=sharing

In [4]:
!pip install gdown
!gdown https://drive.google.com/uc?id=1WYfgr31T-PPwMcxuAq09XZfHQO5Mw8fE
!unzip LibriSpeech-Alignments.zip -d LibriSpeech_Alignments
!rm LibriSpeech-Alignments.zip

Downloading...
From: https://drive.google.com/uc?id=1WYfgr31T-PPwMcxuAq09XZfHQO5Mw8fE
To: /home/chooper/projects/chooper_dl_msdiar/NeMo/tutorials/tools/LibriSpeech-Alignments.zip
100%|██████████████████████████████████████| 71.7M/71.7M [00:01<00:00, 37.9MB/s]
Archive:  LibriSpeech-Alignments.zip
   creating: LibriSpeech_Alignments/LibriSpeech/
   creating: LibriSpeech_Alignments/LibriSpeech/dev-clean/
   creating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/
   creating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/128104/
  inflating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/128104/1272-128104.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/135031/
  inflating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/135031/1272-135031.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/141231/
  inflating: LibriSpeech_Alignments/LibriSpeech/dev-clean/1272/141231/1272-141231.alignment.txt  
   creating: LibriSpeech

  inflating: LibriSpeech_Alignments/LibriSpeech/test-clean/1995/1826/1995-1826.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/1995/1836/
  inflating: LibriSpeech_Alignments/LibriSpeech/test-clean/1995/1836/1995-1836.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/1995/1837/
  inflating: LibriSpeech_Alignments/LibriSpeech/test-clean/1995/1837/1995-1837.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/2094/
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/2094/142345/
  inflating: LibriSpeech_Alignments/LibriSpeech/test-clean/2094/142345/2094-142345.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/2300/
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/2300/131720/
  inflating: LibriSpeech_Alignments/LibriSpeech/test-clean/2300/131720/2300-131720.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/test-clean/237/
   creating: LibriSpeech_Alignments/Lib

  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/298/126791/298-126791.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123504/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123504/302-123504.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123516/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123516/302-123516.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123523/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/302/123523/302-123523.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/307/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/307/127535/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/307/127535/307-127535.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/

   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6563/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6563/285357/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6563/285357/6563-285357.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6563/63821/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6563/63821/6563-63821.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/669/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/669/129061/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/669/129061/669-129061.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/669/129074/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/669/129074/669-129074.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6818/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-100/6818/68772/


  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1289/288043/1289-288043.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1289/288044/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1289/288044/1289-288044.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1290/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1290/135762/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1290/135762/1290-135762.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1296/
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1296/134434/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1296/134434/1296-134434.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1296/138074/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-clean-360/1296/138074/1296-138074.alignment.txt  
   creating: LibriSpeech_Alignme

...

   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/57/121742/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/57/121742/57-121742.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/58/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5825/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5825/50883/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5825/50883/5825-50883.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5825/53035/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5825/53035/5825-53035.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5826/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5826/48845/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5826/48845/5826-48845.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/5826/53496/
  infla

  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/644/162690/644-162690.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/644/162691/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/644/162691/644-162691.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/644/163239/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/644/163239/644-163239.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/70120/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/70120/6459-70120.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/70128/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/70128/6459-70128.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/6459/77766/
  inflating: LibriSpeech_Alignments/Libr

  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7073/83692/7073-83692.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7073/92170/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7073/92170/7073-92170.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/2333/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/2333/7079-2333.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/2343/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/2343/7079-2343.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/89644/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7079/89644/7079-89644.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7092/
   creating: LibriSpeech_Alignments/LibriSpeech/trai

  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7702/96101/7702-96101.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/290368/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/290368/7708-290368.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/293973/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/293973/7708-293973.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/296091/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7708/296091/7708-296091.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7713/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7713/106729/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/7713/106729/7713-106729.alignment.txt  
   creating: LibriSpeech_Alignment

  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8443/274756/8443-274756.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8443/294707/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8443/294707/8443-294707.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8444/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8444/281329/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8444/281329/8444-281329.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8444/283136/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8444/283136/8444-283136.alignment.txt  
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8445/
   creating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8445/281202/
  inflating: LibriSpeech_Alignments/LibriSpeech/train-other-500/8445/281202/8445-281202.alignment.txt  
   creating: LibriSpeech_Alignme

# Step 2: Produce Manifest File with Forced Alignments

The LibriSpeech manifest file and LibriSpeech forced alignments will now be merged into one manifest file for ease of use when generating synthetic data.

In [5]:
!ls
!python NeMo/scripts/speaker_tasks/create_alignment_manifest.py \
  --input_manifest_filepath LibriSpeech/dev_clean.json \
  --base_alignment_path LibriSpeech_Alignments \
  --dataset dev-clean \
  --output_path dev-clean-align.json

CTC_Segmentation_Tutorial.ipynb			 label-studio		 NeMo
Data_Simulator.ipynb				 LibriSpeech
DefinedCrowd_x_NeMo_ASR_Training_Tutorial.ipynb  LibriSpeech_Alignments
[NeMo W 2022-07-25 12:30:18 optimizers:55] Apex was not found. Using the lamb or fused_adam optimizer will error out.
Traceback (most recent call last):
  File "NeMo/scripts/speaker_tasks/create_alignment_manifest.py", line 20, in <module>
    from nemo.collections.asr.parts.utils.manifest_utils import read_manifest, write_manifest
ModuleNotFoundError: No module named 'nemo.collections.asr.parts.utils.manifest_utils'


# Step 3: Download Background Noise Data

The background noise is constructed from https://www.openslr.org/resources/28/rirs_noises.zip (although it can be constructed from other background noise datasets instead)

In [9]:
!wget https://www.openslr.org/resources/28/rirs_noises.zip
!unzip rirs_noises.zip
!rm -r RIRS_NOISES/real_rirs_isotropic_noises/noise_list

Archive:  rirs_noises.zip
   creating: RIRS_NOISES/
   creating: RIRS_NOISES/pointsource_noises/
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0423.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0424.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise_list  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0001.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0002.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0003.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0004.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0005.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0006.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0007.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0008.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0009.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free

  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0114.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0115.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0116.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0117.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0118.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0119.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0120.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0121.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0122.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0123.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0124.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0125.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0126.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-012

  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0232.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0233.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0234.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0235.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0236.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0237.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0238.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0239.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0240.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0241.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0242.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0243.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0244.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-024

  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0348.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0349.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0350.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0351.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0352.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0353.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0354.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0355.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0356.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0357.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0358.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0359.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0360.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-036

  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0473.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0474.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0475.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0476.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0477.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0478.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0480.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0481.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0482.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0483.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0484.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0485.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-0486.wav  
  inflating: RIRS_NOISES/pointsource_noises/noise-free-sound-048

...

  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00023.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00024.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00025.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00026.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00027.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00028.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00029.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00030.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00031.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00032.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00033.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room128-00034.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room128/Room12

  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00056.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00057.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00059.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00058.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00060.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00061.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00062.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00063.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00064.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00065.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00066.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room153-00070.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room153/Room15

  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00001.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00002.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00003.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00004.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00005.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00006.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00007.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00008.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00009.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00010.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00011.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room192-00012.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room192/Room19

  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00018.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00019.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00021.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00022.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00023.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00024.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00025.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00026.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00027.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00028.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00029.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room002-00030.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room002/Room00

  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00023.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00024.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00025.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00026.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00027.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00028.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00029.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00030.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00031.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00032.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00047.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room120-00033.wav  
  inflating: RIRS_NOISES/simulated_rirs/largeroom/Room120/Room12

# Data Simulator Overview

The simulator creates a speech session using utterances from a desired number of speakers. The simulator first selects the LibriSpeech speaker IDs that will be used for the current session, and sets speaker dominance values for each speaker to determine how often each speaker will talk in the session. The session is then constructed by iterating through the following steps:

* The next speaker is selected (which could be the same speaker again with some probability, and which accounts for the speaker dominance values).
* The sentence length is determined using a probability distribution, and an utterance of the desired length is then constructed by concatenating together (or truncating) LibriSpeech sentences corresponding to the desired speaker. Individual word alignments are used to truncate the last LibriSpeech sentence such that the entire utterance has the desired length.
* Next, either the current utterance is overlapped with a previous utterance or silence is introduced before inserting the current utterance. 

The simulator includes a multi-microphone far-field mode that incorporates synthetic room impulse response generation in order to simulate multi-microphone multispeaker sessions. When using RIR generation, the RIR is computed once per batch of sessions, and then each constructed utterance is convolved with the RIR in order to get the sound recorded by each microphone before adding the utterance to the audio session. In this tutorial, only close-talk sessions will be generated.

The simulator also has a speaker enforcement mode which ensures that the correct number of speakers appear in each session, since it is possible that fewer than the desired number may be present since speaker turns are probabilistic. In speaker enforcement mode, the length of the session or speaker probabilites may be adjusted to ensure all speakers are included before the session finishes.

# Parameters

In [11]:
from omegaconf import OmegaConf
conf = OmegaConf.load('NeMo/tools/speech_data_simulator/conf/data_simulator.yaml')
print(OmegaConf.to_yaml(conf))

data_simulator:
  manifest_path: null
  sr: 16000
  random_seed: 42
  session_config:
    num_speakers: 4
    num_sessions: 60
    session_length: 600
  session_params:
    sentence_length_params:
    - 0.4
    - 0.05
    dominance_var: 0.11
    min_dominance: 0.05
    turn_prob: 0.875
    mean_overlap: 0.19
    mean_silence: 0.15
    overlap_prob: 0.5
    start_window: true
    window_type: hamming
    window_size: 0.05
    start_buffer: 0.1
    split_buffer: 0.1
    release_buffer: 0.1
    normalize: true
    normalization_type: equal
    normalization_var: 0.1
    min_volume: 0.75
    max_volume: 1.25
    end_buffer: 0.5
  outputs:
    output_dir: null
    output_filename: diarization_session
    overwrite_output: true
    output_precision: 3
  background_noise:
    add_bg: true
    background_dir: null
    snr: 60
  speaker_enforcement:
    enforce_num_speakers: false
    enforce_time:
    - 0.25
    - 0.75
  segment_manifest:
    window: 0.5
    shift: 0.25
    step_count: 50
    

# Step 3: Generate Simulated Audio Session

A single 4-speaker session of 5 minutes is generated as an example.

In [12]:
!python NeMo/tools/speech_data_simulator/multispeaker_simulator.py \
  --config-path='conf' --config-name='data_simulator.yaml' \
  data_simulator.random_seed=42 \
  data_simulator.manifest_path="dev-clean-align.json" \
  data_simulator.outputs.output_dir="test_closetalk" \
  data_simulator.session_config.num_sessions=1 \
  data_simulator.session_config.session_length=60  \
  data_simulator.background_noise.background_dir="RIRS_NOISES/real_rirs_isotropic_noises"

[NeMo W 2022-07-25 12:49:52 optimizers:55] Apex was not found. Using the lamb or fused_adam optimizer will error out.
Traceback (most recent call last):
  File "NeMo/tools/speech_data_simulator/multispeaker_simulator.py", line 22, in <module>
    from nemo.collections.asr.data.data_simulation import LibriSpeechGenerator, MultiMicLibriSpeechGenerator
ModuleNotFoundError: No module named 'nemo.collections.asr.data.data_simulation'


# Step 4: Listen to and Visualize Session

Listen to the audio and visualize the corresponding speaker timestamps (recorded in a RTTM file for each session)

In [ ]:
import os
import wget
import IPython
import matplotlib.pyplot as plt
import numpy as np
import librosa
from nemo.collections.asr.parts.utils.speaker_utils import rttm_to_labels, labels_to_pyannote_object


ROOT = os.getcwd()
data_dir = os.path.join(ROOT,'test_closetalk')
audio = os.path.join(data_dir,'diarization_session_0.wav')
rttm = os.path.join(data_dir,'diarization_session_0.rttm')

sr = 16000
signal, sr = librosa.load(audio,sr=sr) 

fig,ax = plt.subplots(1,1)
fig.set_figwidth(20)
fig.set_figheight(2)
plt.plot(np.arange(len(signal)),signal,'gray')
fig.suptitle('Synthetic Audio Session', fontsize=16)
plt.xlabel('Time (s)', fontsize=18)
ax.margins(x=0)
plt.ylabel('Signal Strength', fontsize=16);
a,_ = plt.xticks();plt.xticks(a,a/sr);

IPython.display.Audio(audio)

The visualization is useful for seeing both the distribution of utterance lengths, the differing speaker dominance values, and the amount of overlap in the session.

In [ ]:
#display speaker labels for reference
labels = rttm_to_labels(rttm)
reference = labels_to_pyannote_object(labels)
reference

# Files Produced

The following files are produced by the simulator:

* wav files (one per audio session) - the output audio sessions
* rttm files (one per audio session) - the speaker timestamps for the corresponding audio session (used for diarization training)
* json files (one per audio session) - the output manifest file for the corresponding audio session (containing text transcriptions, utterance durations, full paths to audio files, words, and word alignments)
* ctm files (one per audio session) - contains word-by-word alignments, speaker ID, and word
* txt files (one per audio session) - contains the full text transcription for a given session
* list files (one per file type per batch of sessions) - a list of generated files of the given type (wav, rttm, json, ctm, or txt), used primarily for manifest creation


In [ ]:
!ls test_closetalk